# Coursera IBM Data Science Capstone Project

#### Opening a new Supermarket in Los Angeles ,California

•	Build a dataframe of neighborhoods in Los Angeles, California by web scraping the data from Wikipedia page

•	Get the geographical coordinates of the neighborhoods

•	Obtain the venue data for the neighborhoods from Foursquare API

•	Explore and cluster the neighborhoods

•	Select the best cluster to open a new Supermarket


### 1. Importing Libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library
#!conda install -c conda-forge wordcloud==1.4.1 --yes
from wordcloud import WordCloud, get_single_color_func

print("Done.")

Done.


### 2. Get data from Excel file containing Neighborhood Details

In [3]:
# Read files
los_angeles_data=pd.read_excel("D:\study\Coursera\IBM_Data_Science\IBM_DATA_SCIENCE\Final_project_week_4_5\los_angeles_neighborhood_data_new.xlsx")
los_angeles_data

Neighborhood
0                       Angelino Heights
1                           Angeles Mesa
2                          Angelus Vista
3                                 Arleta
4                      Arlington Heights
5                          Arts District
6                        Atwater Village
7                          Baldwin Hills
8                 Baldwin Hills/Crenshaw
9                        Baldwin Village
10                         Baldwin Vista
11                      Beachwood Canyon
12   Bel Air, Bel-Air or Bel Air Estates
13                       Benedict Canyon
14                         Beverly Crest
15                          Beverly Glen
16                         Beverly Grove
17             Beverly Hills Post Office
18                          Beverly Park
19                           Beverlywood
20                         Boyle Heights
21                             Brentwood
22                      Brentwood Circle
23                        Brentwood Glen
24                   Broadway-Manchester
25                             Brookside
26                           Bunker Hill
27                         Cahuenga Pass
28                           Canoga Park
29                     Canterbury Knolls
30                               Carthay
31                        Castle Heights
32                       Central-Alameda
33                          Central City
34                          Century City
35                            Chatsworth
36                   Chesterfield Square
37                         Cheviot Hills
38                             Chinatown
39                          Civic Center
40                              Crenshaw
41                       Crestwood Hills
42                          Cypress Park
43                               Del Rey
44                              Downtown
45                            Eagle Rock
46                     East Gate Bel Air
47                        East Hollywood
48                      East Los Angeles
49                             Echo Park
50                              Edendale
51                             El Sereno
52                          Elysian Park
53                                Encino
54                       Exposition Park
55                    Faircrest Heights 
56                               Fairfax
57                      Fashion District
58                          Filipinotown
59                    Financial District
60                              Florence
61                       Flower District
62                        Franklin Hills
63                           Gallery Row
64                              Garvanza
65                         Glassell Park
66                         Gramercy Park
67                         Granada Hills
68                         Green Meadows
69                         Griffith Park
70                          Hancock Park
71                           Harbor City
72                        Harbor Gateway
73                       Harvard Heights
74                          Harvard Park
75                                Hermon
76                         Highland Park
77                         Historic Core
78                             Hollywood
79                        Hollywood Dell
80                       Hollywood Hills
81                  Hollywood Hills West
82                          Holmby Hills
83                             Hyde Park
84                        Jefferson Park
85                      Jewelry District
86                        Kinney Heights
87                             Koreatown
88                                Ladera
89                      Lafayette Square
90                           Lake Balboa
91                     Lake View Terrace
92                             Larchmont
93                         Laurel Canyon
94                          Leimert Park
95                       Lincoln Heights
96                        Little Armenia
97        

### 3. Get neighborhood coordinates

In [4]:

# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Los Angeles, California'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [5]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in los_angeles_data["Neighborhood"].tolist() ]

In [6]:
coords

[[34.07029000000006, -118.25479999999999],
 [32.764074303732954, -116.98617130920526],
 [34.08757488206556, -118.26715643600681],
 [34.24905000000007, -118.43348999999995],
 [34.03989000000007, -118.32541999999995],
 [33.995992784459574, -118.18689217643083],
 [34.11970000000008, -118.25886999999994],
 [34.021570000000054, -118.36764999999997],
 [34.01043000000004, -118.33665999999994],
 [34.07044548379267, -118.20070982233794],
 [34.07044548379267, -118.20070982233794],
 [34.10915025473649, -118.32045034087673],
 [34.08361000000008, -118.43482999999998],
 [34.093863023638136, -118.42912206311348],
 [34.09653268819107, -118.40329514585207],
 [34.11793000000006, -118.44608999999997],
 [34.09544836979449, -118.42608686997163],
 [34.06147000000004, -118.39871999999997],
 [34.063720000000046, -118.26459999999997],
 [34.05138000000005, -118.40132999999997],
 [34.04004000000003, -118.21049999999997],
 [34.06626000000006, -118.47032999999999],
 [33.98805503453503, -118.27720988461618],
 [33.9

In [7]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [9]:
# merge the coordinates into the original dataframe
los_angeles_data['Latitude'] = df_coords['Latitude']
los_angeles_data['Longitude'] = df_coords['Longitude']

In [12]:
# check the neighborhoods and the coordinates
print(los_angeles_data.shape)
los_angeles_data

(194, 3)


Neighborhood   Latitude   Longitude
0                       Angelino Heights  34.070290 -118.254800
1                           Angeles Mesa  32.764074 -116.986171
2                          Angelus Vista  34.087575 -118.267156
3                                 Arleta  34.249050 -118.433490
4                      Arlington Heights  34.039890 -118.325420
5                          Arts District  33.995993 -118.186892
6                        Atwater Village  34.119700 -118.258870
7                          Baldwin Hills  34.021570 -118.367650
8                 Baldwin Hills/Crenshaw  34.010430 -118.336660
9                        Baldwin Village  34.070445 -118.200710
10                         Baldwin Vista  34.070445 -118.200710
11                      Beachwood Canyon  34.109150 -118.320450
12   Bel Air, Bel-Air or Bel Air Estates  34.083610 -118.434830
13                       Benedict Canyon  34.093863 -118.429122
14                         Beverly Crest  34.096533 -118.403295
15                          Beverly Glen  34.117930 -118.446090
16                         Beverly Grove  34.095448 -118.426087
17             Beverly Hills Post Office  34.061470 -118.398720
18                          Beverly Park  34.063720 -118.264600
19                           Beverlywood  34.051380 -118.401330
20                         Boyle Heights  34.040040 -118.210500
21                             Brentwood  34.066260 -118.470330
22                      Brentwood Circle  33.988055 -118.277210
23                        Brentwood Glen  33.988055 -118.277210
24                   Broadway-Manchester  33.960930 -118.278820
25                             Brookside  34.051243 -118.012597
26                           Bunker Hill  34.052020 -118.250360
27                         Cahuenga Pass  34.124450 -118.342860
28                           Canoga Park  34.202390 -118.601560
29                     Canterbury Knolls  34.233482 -118.549533
30                               Carthay  34.176397 -118.222743
31                        Castle Heights  34.037999 -118.397516
32                       Central-Alameda  33.997420 -118.247780
33                          Central City  34.692127 -118.173804
34                          Century City  34.059440 -118.412810
35                            Chatsworth  34.257250 -118.591010
36                   Chesterfield Square  33.992510 -118.312850
37                         Cheviot Hills  34.034030 -118.410560
38                             Chinatown  34.062290 -118.238370
39                          Civic Center  34.019536 -118.116454
40                              Crenshaw  34.010710 -118.335120
41                       Crestwood Hills  34.130170 -118.191027
42                          Cypress Park  34.094480 -118.226780
43                               Del Rey  33.990820 -118.420620
44                              Downtown  34.048340 -118.255640
45                            Eagle Rock  34.139270 -118.210870
46                     East Gate Bel Air  34.083610 -118.434830
47                        East Hollywood  34.090860 -118.293350
48                      East Los Angeles  34.033470 -118.159090
49                             Echo Park  34.076090 -118.255810
50                              Edendale  34.090680 -118.258480
51                             El Sereno  34.076850 -118.179340
52                          Elysian Park  34.082500 -118.233200
53                                Encino  34.165380 -118.527110
54                       Exposition Park  34.011410 -118.289970
55                    Faircrest Heights   34.090770 -118.078365
56                               Fairfax  34.076100 -118.361220
57                      Fashion District  34.037310 -118.252770
58                          Filipinotown  34.053610 -118.245500
59                    Financial District  37.795780 -122.400480
60                              Florence  33.974750 -118.245390
61                       Flower District  34.047920 -118.258

### 4. Create a map of Los Angeles with neighborhoods superimposed on top

In [17]:
# get the coordinates of Los Angeles
address = 'Los Angeles, California'

geolocator = Nominatim(user_agent="http")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Los Angeles, California {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Los Angeles, California 34.0536909, -118.2427666.


In [18]:
# create map of Los Angeles using latitude and longitude values
map_LA = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(los_angeles_data['Latitude'], los_angeles_data['Longitude'], los_angeles_data['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_LA)  
    
map_LA

In [19]:
# save the map as HTML file
map_LA.save('map_LA.html')

### 5. Use the Foursquare API to explore the neighborhoods

In [20]:
# define Foursquare Credentials and Version
CLIENT_ID = '3X23YXNCVQTROXF2LA3OOLQQ1ZUAFJVJZJY3XVZEUAHRUMAI' # your Foursquare ID
CLIENT_SECRET = 'T1U0CPYBO4DPH4I1AHUFMMWZ33HF43QKMVFRRBXKAD0NBLR1' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 3X23YXNCVQTROXF2LA3OOLQQ1ZUAFJVJZJY3XVZEUAHRUMAI
CLIENT_SECRET:T1U0CPYBO4DPH4I1AHUFMMWZ33HF43QKMVFRRBXKAD0NBLR1


##### Now, let's get the top 100 venues that are within a radius of 2000 meters.

In [21]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(los_angeles_data['Latitude'], los_angeles_data['Longitude'], los_angeles_data['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [22]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(16436, 7)


Neighborhood  Latitude  Longitude            VenueName  VenueLatitude  \
0  Angelino Heights  34.07029  -118.2548      Halliwell Manor      34.069329   
1  Angelino Heights  34.07029  -118.2548             Guisados      34.070262   
2  Angelino Heights  34.07029  -118.2548     Eightfold Coffee      34.071245   
3  Angelino Heights  34.07029  -118.2548  Subliminal Projects      34.072290   
4  Angelino Heights  34.07029  -118.2548          Button Mash      34.073975   

   VenueLongitude          VenueCategory  
0     -118.254165  Performing Arts Venue  
1     -118.250437             Taco Place  
2     -118.250698            Coffee Shop  
3     -118.250737            Art Gallery  
4     -118.251507                 Arcade

In [23]:
#to check for venues per neighborhood
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  \
Neighborhood                                                          
Angeles Mesa                               39         39         39   
Angelino Heights                          100        100        100   
Angelus Vista                             100        100        100   
Arleta                                     56         56         56   
Arlington Heights                         100        100        100   
Arts District                              42         42         42   
Atwater Village                           100        100        100   
Baldwin Hills                              91         91         91   
Baldwin Hills/Crenshaw                     75         75         75   
Baldwin Village                            71         71         71   
Baldwin Vista                              71         71         71   
Beachwood Canyon                          100        100        100   
Bel Air, Bel-Air or Bel Air Estates        62         62         62   
Benedict Canyon                            30         30         30   
Beverly Crest                              41         41         41   
Beverly Glen                               25         25         25   
Beverly Grove                              19         19         19   
Beverly Hills Post Office                 100        100        100   
Beverly Park                              100        100        100   
Beverlywood                               100        100        100   
Boyle Heights                             100        100        100   
Brentwood                                  94         94         94   
Brentwood Circle                           79         79         79   
Brentwood Glen                             79         79         79   
Broadway-Manchester                        53         53         53   
Brookside                                  68         68         68   
Bunker Hill                               100        100        100   
Cahuenga Pass                              83         83         83   
Canoga Park                               100        100        100   
Canterbury Knolls                         100        100        100   
Carthay                                    21         21         21   
Castle Heights                            100        100        100   
Central City                               75         75         75   
Central-Alameda                            48         48         48   
Century City                              100        100        100   
Chatsworth                                 99         99         99   
Chesterfield Square                        62         62         62   
Cheviot Hills                             100        100        100   
Chinatown                                 100        100        100   
Civic Center                              100        100        100   
Crenshaw                                   72         72         72   
Crestwood Hills                           100        100        100   
Cypress Park                               60         60         60   
Del Rey                                   100        100        100   
Downtown                                  100        100        100   
Eagle Rock                                100        100        100   
East Gate Bel Air                          62         62         62   
East Hollywood                            100        100        100   
East Los Angeles                          100        100        100   
Echo Park                                 100        100        100   
Edendale                                  100        100        100   
El Sereno                                  58         58         58   
Elysian Park                              100        100        100   
Encino                                    100        100        100   
Exposition Park                           100        100     

In [24]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 426 uniques categories.


In [25]:
# print out the list of categories
venues_df['VenueCategory'].unique()

array(['Performing Arts Venue', 'Taco Place', 'Coffee Shop',
       'Art Gallery', 'Arcade', 'Japanese Restaurant', 'Sake Bar',
       'American Restaurant', 'Beer Store', 'Massage Studio', 'Bar',
       'Latin American Restaurant', 'Park', 'Bookstore',
       'Vegetarian / Vegan Restaurant', 'Mexican Restaurant',
       'Cocktail Bar', 'Pizza Place', 'Pool', 'Deli / Bodega',
       'Pet Store', 'Food Truck', 'Music Venue', 'Theater',
       'Gym / Fitness Center', 'Health Food Store', 'Café', 'Wine Bar',
       'Circus', 'Gastropub', 'Breakfast Spot', 'Baseball Stadium',
       'Bakery', 'Grocery Store', 'Art Museum', 'Clothing Store',
       'Scenic Lookout', 'Plaza', 'Concert Hall', 'Restaurant',
       'Thai Restaurant', 'Museum', 'Sports Bar', 'Fried Chicken Joint',
       'Yoga Studio', 'Convenience Store', 'Ice Cream Shop',
       'Cajun / Creole Restaurant', 'Jewish Restaurant', 'Burger Joint',
       'Diner', 'Baseball Field', 'Fast Food Restaurant',
       'General Entertainm

In [26]:
# check if the results contain "Supermarket"
"Supermarket" in venues_df['VenueCategory'].unique()

True

In [32]:
len("Supermarket") in venues_df['VenueCategory'].unique()

False

In [36]:
venues_df.to_excel(r'D:\study\Coursera\IBM_Data_Science\File Name.xlsx', index = False)
    

### 6. Analyze Each Neighborhood

In [30]:
# one hot encoding
la_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
la_onehot['Neighborhood'] = venues_df['Neighborhood']
la_onehot['Latitude'] = venues_df['Latitude'] 
la_onehot['Longitude'] = venues_df['Longitude'] 

# move neighborhood column to the first column
fixed_columns = [la_onehot.columns[-1]] + list(la_onehot.columns[:-1])
la_onehot = la_onehot[fixed_columns]

print(la_onehot.shape)
la_onehot.head()

(16436, 428)


Longitude  ATM  Accessories Store  Adult Boutique  Airport  Airport Lounge  \
0  -118.2548    0                  0               0        0               0   
1  -118.2548    0                  0               0        0               0   
2  -118.2548    0                  0               0        0               0   
3  -118.2548    0                  0               0        0               0   
4  -118.2548    0                  0               0        0               0   

   Airport Service  Airport Terminal  American Restaurant  Amphitheater  \
0                0                 0                    0             0   
1                0                 0                    0             0   
2                0                 0                    0             0   
3                0                 0                    0             0   
4                0                 0                    0             0   

   Andhra Restaurant  Antique Shop  Aquarium  Arcade  Argentinian Restaurant  \
0                  0             0         0       0                       0   
1                  0             0         0       0                       0   
2                  0             0         0       0                       0   
3                  0             0         0       0                       0   
4                  0             0         0       1                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            1           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Astrologer  Athletics & Sports  Auditorium  \
0                 0           0                   0           0   
1                 0           0                   0           0   
2                 0           0                   0           0   
3                 0           0                   0           0   
4                 0           0                   0           0   

   Australian Restaurant  Auto Dealership  Auto Garage  Automotive Shop  \
0                      0                0            0                0   
1                      0                0            0                0   
2                      0                0            0                0   
3                      0                0            0                0   
4                      0                0            0                0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0                 0                 0                   0      0   
1                 0                 0                   0      0   
2                 0                 0                   0      0   
3                 0                 0                   0      0   
4                 0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                0         0            0           0              0   
1                0         0            0           0              0   
2                0         0            0           0              0   
3                0         0            0           0              0   
4                0         0            0           0              0   

In [31]:
#group rows by neighborhood and by take the mean of the frequency of occurrence of each category
la_grouped = la_onehot.groupby(["Neighborhood",'Latitude','Longitude']).mean().reset_index()

print(la_grouped.shape)
la_grouped

(194, 428)


Neighborhood   Latitude   Longitude       ATM  \
0                           Angeles Mesa  32.764074 -116.986171  0.000000   
1                       Angelino Heights  34.070290 -118.254800  0.000000   
2                          Angelus Vista  34.087575 -118.267156  0.000000   
3                                 Arleta  34.249050 -118.433490  0.000000   
4                      Arlington Heights  34.039890 -118.325420  0.000000   
5                          Arts District  33.995993 -118.186892  0.023810   
6                        Atwater Village  34.119700 -118.258870  0.010000   
7                          Baldwin Hills  34.021570 -118.367650  0.000000   
8                 Baldwin Hills/Crenshaw  34.010430 -118.336660  0.000000   
9                        Baldwin Village  34.070445 -118.200710  0.000000   
10                         Baldwin Vista  34.070445 -118.200710  0.000000   
11                      Beachwood Canyon  34.109150 -118.320450  0.000000   
12   Bel Air, Bel-Air or Bel Air Estates  34.083610 -118.434830  0.000000   
13                       Benedict Canyon  34.093863 -118.429122  0.000000   
14                         Beverly Crest  34.096533 -118.403295  0.000000   
15                          Beverly Glen  34.117930 -118.446090  0.000000   
16                         Beverly Grove  34.095448 -118.426087  0.000000   
17             Beverly Hills Post Office  34.061470 -118.398720  0.000000   
18                          Beverly Park  34.063720 -118.264600  0.000000   
19                           Beverlywood  34.051380 -118.401330  0.000000   
20                         Boyle Heights  34.040040 -118.210500  0.010000   
21                             Brentwood  34.066260 -118.470330  0.000000   
22                      Brentwood Circle  33.988055 -118.277210  0.000000   
23                        Brentwood Glen  33.988055 -118.277210  0.000000   
24                   Broadway-Manchester  33.960930 -118.278820  0.000000   
25                             Brookside  34.051243 -118.012597  0.000000   
26                           Bunker Hill  34.052020 -118.250360  0.000000   
27                         Cahuenga Pass  34.124450 -118.342860  0.000000   
28                           Canoga Park  34.202390 -118.601560  0.000000   
29                     Canterbury Knolls  34.233482 -118.549533  0.000000   
30                               Carthay  34.176397 -118.222743  0.000000   
31                        Castle Heights  34.037999 -118.397516  0.000000   
32                          Central City  34.692127 -118.173804  0.013333   
33                       Central-Alameda  33.997420 -118.247780  0.000000   
34                          Century City  34.059440 -118.412810  0.000000   
35                            Chatsworth  34.257250 -118.591010  0.000000   
36                   Chesterfield Square  33.992510 -118.312850  0.016129   
37                         Cheviot Hills  34.034030 -118.410560  0.000000   
38                             Chinatown  34.062290 -118.238370  0.000000   
39                          Civic Center  34.019536 -118.116454  0.010000   
40                              Crenshaw  34.010710 -118.335120  0.000000   
41                       Crestwood Hills  34.130170 -118.191027  0.000000   
42                          Cypress Park  34.094480 -118.226780  0.000000   
43                               Del Rey  33.990820 -118.420620  0.000000   
44                              Downtown  34.048340 -118.255640  0.000000   
45                            Eagle Rock  34.139270 -118.210870  0.000000   
46                     East Gate Bel Air  34.083610 -118.434830  0.000000   
47                        East Hollywood  34.090860 -118.293350  0.000000   
48                      East Los Angeles  34.033470 -118.159090  0.000000   
49                             Echo Park  34.076090 -118.255810  0.000000   
50                              Edendale  34.090680 -118.258480  0.000000   
51                      

In [37]:
la_grouped.to_excel(r'D:\study\Coursera\IBM_Data_Science\File_Name.xlsx', index = False)

In [ ]:
len(la_grouped[la_grouped["Supermarket"] > 0])

##### Create a new DataFrame for Supermarket data

In [ ]:
la_market = la_grouped[["Neighborhood","Supermarket"]]

In [ ]:
la_market.head()

### 7. Cluster Neighborhoods

In [15]:
# Finding best k
plt.style.use("seaborn")
Ks = 11
mse = np.zeros((Ks-1))
la_grouped_clustering = la_grouped.drop(['Neighborhood','Latitude','Longitude'], 1)
la_grouped_clustering


NameError: name 'la_grouped' is not defined

In [ ]:
for n in range(1,Ks):
    
    # set number of clusters
    kclusters = n
    # run k-means clustering
    kmeans = KMeans(n_clusters=kclusters, random_state=0, init = 'random', n_init = 15).fit(la_grouped_clustering)
    mse[n-1] = kmeans.inertia_

plt.plot(range(1,Ks),mse)
plt.xlabel("Number of clusters")
plt.ylabel("MSE")
plt.title("K selection")
plt.show()

In [ ]:
# set number of clusters
kclusters = 4

la_clustering = la_market.drop(["Neighborhood"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(la_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

In [ ]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
la_merged = la_market.copy()

# add clustering labels
la_merged["Cluster Labels"] = kmeans.labels_

In [ ]:
la_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
la_merged.head()


In [ ]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
la_merged = la_merged.join(los_angeles_data.set_index("Neighborhood"), on="Neighborhood")

print(la_merged.shape)
la_merged.head()

In [16]:
# sort the results by Cluster Labels
print(la_merged.shape)
la_merged.sort_values(["Cluster Labels"], inplace=True)
la_merged

NameError: name 'la_merged' is not defined

##### visualize the clusters

In [ ]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(la_merged['Latitude'], la_merged['Longitude'], la_merged['Neighborhood'], la_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [ ]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

### 8. Examine Clusters

##### Cluster  0

In [ ]:
cl0 = la_merged.loc[la_merged['Cluster Labels'] == 0]
cl0

##### Cluster 1

In [ ]:
cl1 = la_merged.loc[la_merged['Cluster Labels'] == 1]
cl1

##### Cluster 2

In [ ]:
cl2 = la_merged.loc[la_merged['Cluster Labels'] == 2]
cl2

##### Cluster 3

In [ ]:
cl3 = la_merged.loc[la_merged['Cluster Labels'] == 3]
cl3

### Wordcloud

In [ ]:
word_string = ""
for neighborhood in la_merged["Neighborhood"]:
    elements = ""
    for element in neighborhood.split(","):
        elements += element.strip().replace(" ", "") + " "
    word_string += elements+" "
word_string = word_string.replace(".","")

tmp = cl0["Neighborhood"].tolist()
cl0_list = []
for element in tmp:
    cl0_list.extend(element.split(", "))
cl0_list = [element.replace(" ","") for element in cl0_list]

tmp = cl1["Neighborhood"].tolist()
cl1_list = []
for element in tmp:
    cl1_list.extend(element.split(", "))
cl1_list = [element.replace(" ","") for element in cl1_list]

tmp = cl2["Neighborhood"].tolist()
cl2_list = []
for element in tmp:
    cl2_list.extend(element.split(", "))
cl2_list = [element.replace(" ","") for element in cl2_list]
    
tmp = cl3["Neighborhood"].tolist()
cl3_list = []
for element in tmp:
    cl3_list.extend(element.split(", "))
cl3_list = [element.replace(" ","") for element in cl3_list]
cl3_list = [element.replace(".","") for element in cl3_list]



cl1_list

In [ ]:
class GroupedColorFunc(object):
    """Create a color function object which assigns DIFFERENT SHADES of
       specified colors to certain words based on the color to words mapping.

       Uses wordcloud.get_single_color_func

       Parameters
       ----------
       color_to_words : dict(str -> list(str))
         A dictionary that maps a color to the list of words.

       default_color : str
         Color that will be assigned to a word that's not a member
         of any value from color_to_words.
    """

    def __init__(self, color_to_words, default_color):
        self.color_func_to_words = [
            (get_single_color_func(color), set(words))
            for (color, words) in color_to_words.items()]

        self.default_color_func = get_single_color_func(default_color)

    def get_color_func(self, word):
        """Returns a single_color_func associated with the word"""
        try:
            color_func = next(
                color_func for (color_func, words) in self.color_func_to_words
                if word in words)
        except StopIteration:
            color_func = self.default_color_func

        return color_func

    def __call__(self, word, **kwargs):
        return self.get_color_func(word)(word, **kwargs)

wordcloud = WordCloud(width=1000, height=600, background_color='white', max_words = 500).generate(word_string)

color_to_words = {
    # words below will be colored with a green single color function
    'yellow': cl0_list,
    # will be colored with a red single color function
    'black': cl1_list,
    'blue': cl2_list,
    '#00ff00': cl3_list
}

default_color = 'grey'

print('Word cloud created!')

fig = plt.figure()
fig.set_figwidth(500)
fig.set_figheight(10)

grouped_color_func = GroupedColorFunc(color_to_words, default_color)

# Apply our color function
wordcloud.recolor(color_func=grouped_color_func)

plt.imshow(wordcloud, interpolation="bilinear")
plt.axis('off')
plt.show()

## Conclusion :


###### Based on the clustering of neighborhoods, we can see that Cluster 1 has no Supermarkets followed by some supermarkets in cluster 2 ,cluster 0 and cluster 3 respectively. It would be a good option to open a Supermarket in any of the neighborhoods that fall under Cluster 0. In order to decide a neighborhood within cluster 0 we can improve this analysis using 2 more criterias. First criteria would be to analyze those neighborhoods based on their population as higher population will lead to more customers in the supermarket which is highly essential for new businesses. Second criteria to be considered is the cost of land as this would highly affect the Return on Investment factor of the Supermarket. For this , we can analyze the cost of land for each neighborhood falling under cluster 0 and look for the cheaper options to open a Supermarket. Considering these conditions, the best case scenario to open a supermarket would be in a neighborhood with high population and low cost of land as this will Increase Return on Inverstment and ensure stable income due to high population.